In [1]:
# Baixar as dependências
%pip install scipy numpy requests 

# Importar dependências
import io
import numpy as np
import requests as rq
import IPython.display as ipd
from scipy.interpolate import interp1d
from scipy.io import wavfile

# Mude essa constante pra aumentar/diminuir a compressão
COMPRESSION_FACTOR = 5

# URL para buscar áudio no github
AUDIO_URL = 'https://github.com/RexynyN/current-semester/raw/main/CS/audio.wav'

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [2]:

# Função de utilidade para aplicar a transformação 
def apply(signal, transfer, interpolation='linear'):
    constant = np.linspace(-1, 1, len(transfer))
    interpolator = interp1d(constant, transfer, interpolation)
    return interpolator(signal)

# Compressor de amplitude do áudio (usando arco-tangente)
def arctan_compressor(x, factor=2):
    constant = np.linspace(-1, 1, 1000)
    transfer = np.arctan(factor * constant)
    transfer /= np.abs(transfer).max()
    transfer = assert_range(transfer)
    return apply(x, transfer)

# Faz um check para valores maiores que os limites por causa da 
# imprecisão de floats ex: 1.00000084729
def assert_range(x):
    mask = (x > 1)
    x[mask] = 1
    mask = (x < -1)
    x[mask] = -1
    return x 

# Orquestração das transformações (local)
def transform_audio_local(filename, factor=2):
    sr, x = wavfile.read(filename)
    # Deixa ele entre -1 <= x <= 1
    x = x / np.abs(x).max() 
    x = assert_range(x)

    comp = arctan_compressor(x, factor)
    comp = np.int16(comp * 32767)

    new_file = filename.split(".")[0]
    new_file += "-tranformed.wav"
    wavfile.write(new_file, sr, comp)

# Orquestração das transformações (baixar audio de uma fonte online)
def transform_audio_online(factor=2):
    resposta = rq.get(AUDIO_URL) # Fazemos a requisição para a API
    sr, x = wavfile.read(io.BytesIO(resposta.content))

    # Deixa ele entre -1 <= x <= 1
    x = x / np.abs(x).max() 
    x = assert_range(x)

    comp = arctan_compressor(x, factor)
    comp = np.int16(comp * 32767)

    return sr, comp.T

sr, audio = transform_audio_online(COMPRESSION_FACTOR)


## Áudio Original

In [3]:
resposta = rq.get(AUDIO_URL)
og_rate, og_audio = wavfile.read(io.BytesIO(resposta.content))

ipd.Audio(og_audio.T, rate=og_rate, autoplay=True) 

## Áudio Comprimido

In [4]:
ipd.Audio(audio, rate=sr, autoplay=True)